# Human Entity in Al Qur'an with NER & Rule Based

Import Modules

In [1]:
import pandas as pd

## 1. Buckwalter
Mengubah form latin dalam dataset qorpus menjadi arab

In [2]:
# Install module
# pip install lang-trans

In [3]:
# Import package
from lang_trans.arabic import buckwalter

In [4]:
# Import Dataset
quranicDF = pd.read_excel('./Dataset/quranic-corpus-morphology-0.4.xlsx', index_col=0)

In [5]:
# Show first 5 row data
quranicDF.head()

FORM  TAG                                    FEATURES
LOCATION                                                              
(1:1:1:1)          bi    P                                  PREFIX|bi+
(1:1:1:2)        somi    N          STEM|POS:N|LEM:{som|ROOT:smw|M|GEN
(1:1:2:1)     {ll~ahi   PN         STEM|POS:PN|LEM:{ll~ah|ROOT:Alh|GEN
(1:1:3:1)          {l  DET                                  PREFIX|Al+
(1:1:3:2)  r~aHoma`ni  ADJ  STEM|POS:ADJ|LEM:r~aHoma`n|ROOT:rHm|MS|GEN

In [6]:
# First Buckwaltering
arab = []

for i in range (len(quranicDF)):
    if (pd.isna(quranicDF.iloc[i,0])):
        arab.append("")
    else:
        arab.append(buckwalter.untransliterate(quranicDF.iloc[i,0]))
    (str(i) + ' ' +arab[i])

#### Second Bucwaltering
Menghilangkan 3 char yang aneh dan mereplace 1 char lalu bucwaltering semuanya ke arab

In [7]:
# Import package regular expression
import re

arab = []

for i in range (len(quranicDF)):
    
    if (pd.isna(quranicDF.iloc[i,0])):
        arab.append("")
    else:
    
        quranicDF.iloc[i,0] = re.sub(r'^aA', 'A`', quranicDF.iloc[i,0]) #belum paham parameter string/df.iloc[i,0] #Done

        if quranicDF.iloc[i,0] == 'a':
            arab.append(quranicDF.iloc[i,0].replace(r'^a$', '>a')) #belum paham $ nya #Done
        else:
            arab.append(buckwalter.untransliterate(quranicDF.iloc[i,0]))
            
        arab[i] = arab[i].replace('^', '')
        arab[i] = arab[i].replace('@', '')
        arab[i] = arab[i].replace('[', '')
    str(i) + ' ' + arab[i]

In [8]:
# insert data to variable
quranicDF['ARAB'] = arab
arab

['بِ',
 'سْمِ',
 'ٱللَّهِ',
 'ٱل',
 'رَّحْمَٰنِ',
 'ٱل',
 'رَّحِيمِ',
 'ٱلْ',
 'حَمْدُ',
 'لِ',
 'لَّهِ',
 'رَبِّ',
 'ٱلْ',
 'عَٰلَمِينَ',
 'ٱل',
 'رَّحْمَٰنِ',
 'ٱل',
 'رَّحِيمِ',
 'مَٰلِكِ',
 'يَوْمِ',
 'ٱل',
 'دِّينِ',
 'إِيَّاكَ',
 'نَعْبُدُ',
 'وَ',
 'إِيَّاكَ',
 'نَسْتَعِينُ',
 'ٱهْدِ',
 'نَا',
 'ٱل',
 'صِّرَٰطَ',
 'ٱلْ',
 'مُسْتَقِيمَ',
 'صِرَٰطَ',
 'ٱلَّذِينَ',
 'أَنْعَمْ',
 'تَ',
 'عَلَيْ',
 'هِمْ',
 'غَيْرِ',
 'ٱلْ',
 'مَغْضُوبِ',
 'عَلَيْ',
 'هِمْ',
 'وَ',
 'لَا',
 'ٱل',
 'ضَّالِّينَ',
 'الم',
 'ذَٰلِكَ',
 'ٱلْ',
 'كِتَٰبُ',
 'لَا',
 'رَيْبَ',
 'فِي',
 'هِ',
 'هُدًى',
 'لِّ',
 'لْ',
 'مُتَّقِينَ',
 'ٱلَّذِينَ',
 'يُؤْمِنُ',
 'ونَ',
 'بِ',
 'ٱلْ',
 'غَيْبِ',
 'وَ',
 'يُقِيمُ',
 'ونَ',
 'ٱل',
 'صَّلَوٰةَ',
 'وَ',
 'مِ',
 'مَّا',
 'رَزَقْ',
 'نَٰ',
 'هُمْ',
 'يُنفِقُ',
 'ونَ',
 'وَ',
 'ٱلَّذِينَ',
 'يُؤْمِنُ',
 'ونَ',
 'بِ',
 'مَا',
 'أُنزِلَ',
 'إِلَيْ',
 'كَ',
 'وَ',
 'مَا',
 'أُنزِلَ',
 'مِن',
 'قَبْلِ',
 'كَ',
 'وَ',
 'بِ',
 'ٱلْ',
 'اٰخِرَةِ',
 'هُمْ',
 'يُوقِنُ',
 'ونَ',


In [9]:
# export data
quranicDF.to_excel("./Output/quranic-corpus-morphology-0.4-with-arab.xlsx")
# quranic_df.to_csv("./Output/quranic-corpus-morphology-0.4-with-arab.csv")

## 2. Get Human Entity Rule

In [10]:
# Import dataset
entityDF = pd.read_excel('./Dataset/human-entity-juz-3.xlsx')
pd.set_option('display.max_rows', 999999)

In [11]:
def findHumanEntityPatterns(file):
    
    tempPatterns = [[]]
    finalPatterns = []
    currentTag = 0
    opentagCount = 0
    df = pd.DataFrame({'pattern': []})
    
    for i in range(len(file)):

        closetags = [char for char in str(file.at[i, "closetag"])]
        opentags = [char for char in str(file.at[i, "opentag"])]

        for j in range(len(opentags)):
            if opentags[j] == '(':
                opentagCount += 1

        if opentagCount > 0:
            tempPatterns[currentTag].append(file.at[i, "tag"])

        for k in range(len(closetags)):
            if closetags[k] == ')':
                if opentagCount == 1:
                    toInput = (str(tempPatterns[currentTag]))
                    df = df.append({'pattern' : toInput}, ignore_index=True)
                    finalPatterns.append(tempPatterns[currentTag])
                    currentTag += 1
                    tempPatterns.append([])
                opentagCount -= 1
                
    if tempPatterns[len(tempPatterns)-1] == []:
        del tempPatterns[len(tempPatterns)-1]

    # Ini apaan coba
    tempPatterns = set(tuple(element) for element in tempPatterns)
    tempPatterns = [list(t) for t in set(tuple(element) for element in tempPatterns)]    
        
    return tempPatterns
#     return df

In [12]:
patterns = findHumanEntityPatterns(entityDF)

Use return df for good looking data

In [13]:
# print (len(patterns))
# patterns

Remove Duplicate

In [14]:
# patterns = patterns.drop_duplicates(subset=None, keep='first', inplace=False)
# print(len(patterns))
# patterns

## 3. Set Human Entity Rule

In [18]:
# Import data
quranicArab = pd.read_excel('./Output/quranic-corpus-morphology-0.4-with-arab.xlsx', encoding='utf8')
pd.set_option('display.max_rows', 999999) # Untuk menampilkan semua data sekaligus

In [19]:
# Prepare data
def convertAndGroupToArray(data):
    
    ayats = [[]]

    for index, row in data.iterrows():
        location = row['LOCATION']
        ayat = location.split(':')[1]
        data.at[index, 'LOCATION'] = ayat

    length = len(data)
    i = 0
    data.at[0, 'LOCATION'] = 0
    
    for index, row in data.iterrows():
        
        # tokenizing location
        if index < length-1:
            currentLocation = row['LOCATION']
            nextLocation = data.at[index+1, 'LOCATION']

            if index == length-2 or currentLocation != nextLocation:
                i = i+1
                ayats.append([])
            
            data.at[index, 'LOCATION'] = i
            
            words = {
                'OPEN TAG' : '',
                'AYAT' : int(row['LOCATION']),
                'ARAB' : row['ARAB'],
                'TAG' : row['TAG'],
                'CLOSE TAG' : ''
            }
            
            ayats[i].append(words)
    
    return ayats
     
ayats = convertAndGroupToArray(quranicArab[:5000])

In [20]:
# Rule based logic
def findHumanEntity(ayats):
    
    ayatIndex = 0
    entityIndex = 0
    for ayat in ayats:
        for pattern in patterns:
            patternLength = len(pattern)
            for wordIndex in range(len(ayat) - patternLength):
                # Get set of words based on the pattern length
                wordTagsSet = []
                for wordOfSetIndex in range((patternLength)):
                    wordTagsSet.append(ayat[wordIndex+wordOfSetIndex]['TAG'])
                if str(wordTagsSet) == str(pattern):
                    ayat[wordIndex]['OPEN TAG'] += str(entityIndex) + '('
                    ayat[wordIndex+patternLength]['CLOSE TAG'] += str(entityIndex) + ')'
                    entityIndex += 1
        ayatIndex += 1
                
findHumanEntity(ayats)

In [21]:
ayatDF = pd.DataFrame({'AYAT': [], 'OPEN TAG': [], 'ARAB': [], 'TAG': [], 'CLOSE TAG': []});

ayatCollections = []
openTagCollections = []
arabCollections = []
tagCollections = []
closeTagCollections = []

for ayat in ayats:
    for word in ayat:
        ayatDF = ayatDF.append({'AYAT': word['AYAT'], 'OPEN TAG': word['OPEN TAG'], 'ARAB': word['ARAB'], 'TAG': word['TAG'], 'CLOSE TAG': word['CLOSE TAG']}, ignore_index=True)
        
ayatDF

AYAT         OPEN TAG             ARAB   TAG        CLOSE TAG
0       1.0                                بِ     P                 
1       1.0             1(3(             سْمِ     N                 
2       1.0               0(          ٱللَّهِ    PN               1)
3       1.0                                ٱل   DET             0)3)
4       1.0               2(       رَّحْمَٰنِ   ADJ                 
5       1.0                                ٱل   DET               2)
6       2.0               7(         رَّحِيمِ   ADJ                 
7       2.0               8(              ٱلْ   DET               7)
8       2.0               5(           حَمْدُ     N                 
9       2.0                                لِ     P             5)8)
10      2.0               4(            لَّهِ    PN                 
11      2.0               6(            رَبِّ     N               4)
12      2.0                               ٱلْ   DET               6)
13      3.0            9(10(       عَٰلَمِينَ     N                 
14      3.0                                ٱل   DET              10)
15      3.0              11(       رَّحْمَٰنِ   ADJ                 
16      3.0                                ٱل   DET            9)11)
17      4.0              14(         رَّحِيمِ   ADJ                 
18      4.0              12(          مَٰلِكِ     N              14)
19      4.0              13(           يَوْمِ     N              12)
20      4.0                                ٱل   DET              13)
21      5.0           15(16(           دِّينِ     N                 
22      5.0                          إِيَّاكَ  PRON              16)
23      5.0                          نَعْبُدُ     V              15)
24      5.0                                وَ  CONJ                 
25      5.0                          إِيَّاكَ  PRON                 
26      6.0                       نَسْتَعِينُ     V                 
27      6.0                             ٱهْدِ     V                 
28      6.0                               نَا  PRON                 
29      6.0              18(               ٱل   DET                 
30      6.0              17(         صِّرَٰطَ     N                 
31      6.0                               ٱلْ   DET           17)18)
32      7.0              24(      مُسْتَقِيمَ   ADJ                 
33      7.0              21(          صِرَٰطَ     N              24)
34      7.0           20(26(        ٱلَّذِينَ   REL              21)
35      7.0                          أَنْعَمْ     V                 
36      7.0                                تَ  PRON              20)
37      7.0                            عَلَيْ     P              26)
38      7.0                              هِمْ  PRON                 
39      7.0           19(22(           غَيْرِ     N                 
40      7.0              25(              ٱلْ   DET              22)
41      7.0              23(        مَغْضُوبِ     N                 
42      7.0                            عَلَيْ     P        19)23)25)
43      7.0                              هِمْ  PRON                 
44      7.0                                وَ  CONJ                 
45      7.0                               لَا   NEG                 
46      7.0                                ٱل   DET                 
47      8.0                        ضَّالِّينَ     N                 
48      9.0                               الم   INL                 
49      9.0                           ذَٰلِكَ   DEM                 
50      9.0              30(              ٱلْ   DET                 
51      9.0              27(          كِتَٰبُ     N                 
52      9.0                               لَا   NEG           27)30)
53      9.0              28(           رَيْبَ     N                 
54      9.0                               فِي     P              28)
55      9.0                                هِ  PRON                 
56      9.0              29(            هُدًى     N                 
57   

## 4. Placing Space

In [22]:
dataForEntity = pd.read_excel('./Output/quranic-corpus-morphology-0.4-with-arab.xlsx')
dataOfStandardizationResource = pd.read_excel('./Dataset/wordbywordFromCorpus.xlsx')

def strip_arabic_vowels(line_with_vowels):
    diacritics = [u'\u064e',  # fatha, short a
                  u'\u064b',  # double fatha
                  u'\u0650',  # kasra, short i
                  u'\u064d',  # double kasra
                  u'\u064f',  # damma, short u
                  u'\u064c',  # double damma
                  u'\u0652',  # sukkun, nothing
                  u'\u0651',  # shedda, double
                  u'\u0670',
                  u'\u0671',
                  u'\u0653',
                  u'\u08EA',
                  u'\uFBB2',
                  u'\u0660',
                  u'\u06DF',
                  u'\u06E2',
                  u'\u06E5',
                  ',',
                  '.',
                  u'\u06E7',
                  u'\u06E6',
                  u'\u0654',
                  u'\u06ED',
                  '#',
                  '[',
                  ']',
                  ':',
                  u'\u06DC',
                  '"',
                  u'\u06e0',
                  u'\u06e8'
                 ]
    
    line_without_vowels = ''
    for char in line_with_vowels:
        if char not in diacritics:
            line_without_vowels += char
    
    return line_without_vowels
    
dosrIndex = 0

import re

for i in range(len(dataForEntity)):
    query = strip_arabic_vowels(str(dataForEntity.at[i, 'ARAB']))
    nextQuery = strip_arabic_vowels(str(dataForEntity.at[i+1, 'ARAB']))
    source = strip_arabic_vowels(str(dataOfStandardizationResource.at[dosrIndex, 'Data']))
    
    print(str(i) + ' | ' + query + ' | ' + source)
    
    exist = re.search(query + "$", source)
    queryLocation = -1
    
    nextQueryExist = re.search(nextQuery + "$", source)

    if exist is not None:
        queryLocation = exist.span()[0]
    
    if nextQueryExist is not None:
        if nextQueryExist.span()[0] == 0:
            nextQueryExist = False
            
    queryShouldLastIndex = len(source) - len(query)
    
    if exist and queryShouldLastIndex == queryLocation:
        dataForEntity.at[i, 'SPACE AFTER'] = 'TRUE'
        print("Last")
        dosrIndex += 1
    else:
        print("Not last") 
            
# pd.set_option("display.max_rows", 99999999)
dataForEntity

0 | ب | بسم
Not last
1 | سم | بسم
Last
2 | لله | لله
Last
3 | ل | لرحمن
Not last
4 | رحمن | لرحمن
Last
5 | ل | لرحيم
Not last
6 | رحيم | لرحيم
Last
7 | ل | لحمد
Not last
8 | حمد | لحمد
Last
9 | ل | لله
Not last
10 | له | لله
Last
11 | رب | رب
Last
12 | ل | لعلمين
Not last
13 | علمين | لعلمين
Last
14 | ل | لرحمن
Not last
15 | رحمن | لرحمن
Last
16 | ل | لرحيم
Not last
17 | رحيم | لرحيم
Last
18 | ملك | ملك
Last
19 | يوم | يوم
Last
20 | ل | لدين
Not last
21 | دين | لدين
Last
22 | إياك | إياك
Last
23 | نعبد | نعبد
Last
24 | و | وإياك
Not last
25 | إياك | وإياك
Last
26 | نستعين | نستعين
Last
27 | هد | هدنا
Not last
28 | نا | هدنا
Last
29 | ل | لصرط
Not last
30 | صرط | لصرط
Last
31 | ل | لمستقيم
Not last
32 | مستقيم | لمستقيم
Last
33 | صرط | صرط
Last
34 | لذين | لذين
Last
35 | أنعم | أنعمت
Not last
36 | ت | أنعمت
Last
37 | علي | عليهم
Not last
38 | هم | عليهم
Last
39 | غير | غير
Last
40 | ل | لمغضوب
Not last
41 | مغضوب | لمغضوب
Last
42 | علي | عليهم
Not last
43 | هم | عليهم
Last
44 | و | ولا


Last
492 | كن | كنتم
Not last
493 | تم | كنتم
Last
494 | فى | فى
Last
495 | ريب | ريب
Last
496 | م | مما
Not last
497 | ما | مما
Last
498 | نزل | نزلنا
Not last
499 | نا | نزلنا
Last
500 | على | على
Last
501 | عبد | عبدنا
Not last
502 | نا | عبدنا
Last
503 | ف | فأتوا
Not last
504 | أت | فأتوا
Not last
505 | وا | فأتوا
Last
506 | ب | بسورة
Not last
507 | سورة | بسورة
Last
508 | من | من
Last
509 | مثل | مثله
Not last
510 | ه | مثله
Last
511 | و | ودعوا
Not last
512 | دع | ودعوا
Not last
513 | وا | ودعوا
Last
514 | شهداء | شهداءكم
Not last
515 | كم | شهداءكم
Last
516 | من | من
Last
517 | دون | دون
Last
518 | لله | لله
Last
519 | إن | إن
Last
520 | كن | كنتم
Not last
521 | تم | كنتم
Last
522 | صدقين | صدقين
Last
523 | ف | فإن
Not last
524 | إن | فإن
Last
525 | لم | لم
Last
526 | تفعل | تفعلوا
Not last
527 | وا | تفعلوا
Last
528 | و | ولن
Not last
529 | لن | ولن
Last
530 | تفعل | تفعلوا
Not last
531 | وا | تفعلوا
Last
532 | ف | فتقوا
Not last
533 | تق | فتقوا
Not last
534 | وا | فتقوا
Last

978 | ه | عليه
Last
979 | إن | إنه
Not last
980 | ه | إنه
Last
981 | هو | هو
Last
982 | ل | لتواب
Not last
983 | تواب | لتواب
Last
984 | ل | لرحيم
Not last
985 | رحيم | لرحيم
Last
986 | قل | قلنا
Not last
987 | نا | قلنا
Last
988 | هبط | هبطوا
Not last
989 | وا | هبطوا
Last
990 | من | منها
Not last
991 | ها | منها
Last
992 | جميعا | جميعا
Last
993 | ف | فإما
Not last
994 | إما | فإما
Last
995 | يأتي | يأتينكم
Not last
996 | ن | يأتينكم
Not last
997 | كم | يأتينكم
Last
998 | من | منى
Not last
999 | ى | منى
Last
1000 | هدى | هدى
Last
1001 | ف | فمن
Not last
1002 | من | فمن
Last
1003 | تبع | تبع
Last
1004 | هدا | هداى
Not last
1005 | ى | هداى
Last
1006 | ف | فلا
Not last
1007 | لا | فلا
Last
1008 | خوف | خوف
Last
1009 | علي | عليهم
Not last
1010 | هم | عليهم
Last
1011 | و | ولا
Not last
1012 | لا | ولا
Last
1013 | هم | هم
Last
1014 | يحزن | يحزنون
Not last
1015 | ون | يحزنون
Last
1016 | و | ولذين
Not last
1017 | لذين | ولذين
Last
1018 | كفر | كفروا
Not last
1019 | وا | كفروا
Last
1020 | و

Not last
1671 | ون | يعتدون
Last
1672 | إن | إن
Last
1673 | لذين | لذين
Last
1674 | امن | ءامنوا
Not last
1675 | وا | ءامنوا
Last
1676 | و | ولذين
Not last
1677 | لذين | ولذين
Last
1678 | هاد | هادوا
Not last
1679 | وا | هادوا
Last
1680 | و | ولنصرى
Not last
1681 | ل | ولنصرى
Not last
1682 | نصرى | ولنصرى
Last
1683 | و | ولصبـين
Not last
1684 | ل | ولصبـين
Not last
1685 | صبـين | ولصبـين
Last
1686 | من | من
Last
1687 | امن | ءامن
Last
1688 | ب | بلله
Not last
1689 | لله | بلله
Last
1690 | و | وليوم
Not last
1691 | ل | وليوم
Not last
1692 | يوم | وليوم
Last
1693 | ل | لءاخر
Not last
1694 | اخر | لءاخر
Last
1695 | و | وعمل
Not last
1696 | عمل | وعمل
Last
1697 | صلحا | صلحا
Last
1698 | ف | فلهم
Not last
1699 | ل | فلهم
Not last
1700 | هم | فلهم
Last
1701 | أجر | أجرهم
Not last
1702 | هم | أجرهم
Last
1703 | عند | عند
Last
1704 | رب | ربهم
Not last
1705 | هم | ربهم
Last
1706 | و | ولا
Not last
1707 | لا | ولا
Last
1708 | خوف | خوف
Last
1709 | علي | عليهم
Not last
1710 | هم | عليهم
Last
1711

Not last
2225 | نار | لنار
Last
2226 | إلا | إلا
Last
2227 | أياما | أياما
Last
2228 | معدودة | معدودة
Last
2229 | قل | قل
Last
2230 | أ | أتخذتم
Not last
2231 | تخذ | أتخذتم
Not last
2232 | تم | أتخذتم
Last
2233 | عند | عند
Last
2234 | لله | لله
Last
2235 | عهدا | عهدا
Last
2236 | ف | فلن
Not last
2237 | لن | فلن
Last
2238 | يخلف | يخلف
Last
2239 | لله | لله
Last
2240 | عهد | عهده
Not last
2241 | ه | عهده
Last
2242 | أم | أم
Last
2243 | تقول | تقولون
Not last
2244 | ون | تقولون
Last
2245 | على | على
Last
2246 | لله | لله
Last
2247 | ما | ما
Last
2248 | لا | لا
Last
2249 | تعلم | تعلمون
Not last
2250 | ون | تعلمون
Last
2251 | بلى | بلى
Last
2252 | من | من
Last
2253 | كسب | كسب
Last
2254 | سيئة | سيئة
Last
2255 | و | وأحطت
Not last
2256 | أحطت | وأحطت
Last
2257 | ب | به
Not last
2258 | ه | به
Last
2259 | خطيـت | خطيـته
Not last
2260 | ه | خطيـته
Last
2261 | ف | فأولئك
Not last
2262 | أولئك | فأولئك
Last
2263 | أصحب | أصحب
Last
2264 | ل | لنار
Not last
2265 | نار | لنار
Last
2266 | هم | 

...

126779 | فى | يأجوج
Not last
126780 | كبد | يأجوج
Not last
126781 | أ | يأجوج
Not last
126782 | يحسب | يأجوج
Not last
126783 | أن | يأجوج
Not last
126784 | لن | يأجوج
Not last
126785 | يقدر | يأجوج
Not last
126786 | علي | يأجوج
Not last
126787 | ه | يأجوج
Not last
126788 | أحد | يأجوج
Not last
126789 | يقول | يأجوج
Not last
126790 | أهلك | يأجوج
Not last
126791 | ت | يأجوج
Not last
126792 | مالا | يأجوج
Not last
126793 | لبدا | يأجوج
Not last
126794 | أ | يأجوج
Not last
126795 | يحسب | يأجوج
Not last
126796 | أن | يأجوج
Not last
126797 | لم | يأجوج
Not last
126798 | ير | يأجوج
Not last
126799 | ه | يأجوج
Not last
126800 | أحد | يأجوج
Not last
126801 | أ | يأجوج
Not last
126802 | لم | يأجوج
Not last
126803 | نجعل | يأجوج
Not last
126804 | ل | يأجوج
Not last
126805 | ه | يأجوج
Not last
126806 | عينين | يأجوج
Not last
126807 | و | يأجوج
Not last
126808 | لسانا | يأجوج
Not last
126809 | و | يأجوج
Not last
126810 | شفتين | يأجوج
Not last
126811 | و | يأجوج
Not last
126812 | هدي | يأجوج
Not 

Not last
127251 | طور | يأجوج
Not last
127252 | سينين | يأجوج
Not last
127253 | و | يأجوج
Not last
127254 | هذا | يأجوج
Not last
127255 | ل | يأجوج
Not last
127256 | بلد | يأجوج
Not last
127257 | ل | يأجوج
Not last
127258 | أمين | يأجوج
Not last
127259 | ل | يأجوج
Not last
127260 | قد | يأجوج
Not last
127261 | خلق | يأجوج
Not last
127262 | نا | يأجوج
Not last
127263 | ل | يأجوج
Not last
127264 | إنسن | يأجوج
Not last
127265 | فى | يأجوج
Not last
127266 | أحسن | يأجوج
Not last
127267 | تقويم | يأجوج
Not last
127268 | ثم | يأجوج
Not last
127269 | ردد | يأجوج
Not last
127270 | ن | يأجوج
Not last
127271 | ه | يأجوج
Not last
127272 | أسفل | يأجوج
Not last
127273 | سفلين | يأجوج
Not last
127274 | إلا | يأجوج
Not last
127275 | لذين | يأجوج
Not last
127276 | امن | يأجوج
Not last
127277 | وا | يأجوج
Not last
127278 | و | يأجوج
Not last
127279 | عمل | يأجوج
Not last
127280 | وا | يأجوج
Not last
127281 | ل | يأجوج
Not last
127282 | صلحت | يأجوج
Not last
127283 | ف | يأجوج
Not last
127284 | ل | يأ

Not last
127800 | تعلم | يأجوج
Not last
127801 | ون | يأجوج
Not last
127802 | ثم | يأجوج
Not last
127803 | كلا | يأجوج
Not last
127804 | سوف | يأجوج
Not last
127805 | تعلم | يأجوج
Not last
127806 | ون | يأجوج
Not last
127807 | كلا | يأجوج
Not last
127808 | لو | يأجوج
Not last
127809 | تعلم | يأجوج
Not last
127810 | ون | يأجوج
Not last
127811 | علم | يأجوج
Not last
127812 | ل | يأجوج
Not last
127813 | يقين | يأجوج
Not last
127814 | ل | يأجوج
Not last
127815 | ترو | يأجوج
Not last
127816 | ن | يأجوج
Not last
127817 | ل | يأجوج
Not last
127818 | جحيم | يأجوج
Not last
127819 | ثم | يأجوج
Not last
127820 | ل | يأجوج
Not last
127821 | ترو | يأجوج
Not last
127822 | ن | يأجوج
Not last
127823 | ها | يأجوج
Not last
127824 | عين | يأجوج
Not last
127825 | ل | يأجوج
Not last
127826 | يقين | يأجوج
Not last
127827 | ثم | يأجوج
Not last
127828 | ل | يأجوج
Not last
127829 | تسـل | يأجوج
Not last
127830 | ن | يأجوج
Not last
127831 | يومئذ | يأجوج
Not last
127832 | عن | يأجوج
Not last
127833 | ل | يأجوج


Not last
128213 | من | يأجوج
Not last
128214 | ل | يأجوج
Not last
128215 | جنة | يأجوج
Not last
128216 | و | يأجوج
Not last
128217 | ل | يأجوج
Not last


KeyError: 128219

berhenti di 74359

In [23]:
dataForEntity.to_excel("./Output/quranic-corpus-morphology-0.4-with-arab-and-space.xlsx")

## 5. Insert Dataset & Rule to Mongo

In [ ]:
# import package
import pymongo

# connecting to mongo
myclient = pymongo.MongoClient("mongodb://localhost:27017/")

# create database
mydb = myclient["TA"]

# create collection
quran = mydb["quran"]

# import dataset
data = pd.read_excel("./Output/quranic-corpus-morphology-0.4-with-arab-and-space.xlsx")

Split location dataset

In [ ]:
for i in range(len(data)):
    location = data.at[i, "LOCATION"]
    location = location.split(':')
    no_surat = location[0][1:] # belum paham
    ayat = location[1]
    word = location[2]
    
    data.at[i, 'SURAH_NUMBER'] = no_surat
    data.at[i, 'AYAT_NUMBER'] = ayat
    data.at[i, 'WORD_NUMBER'] = word

In [ ]:
# cek data
data.iloc[5]

In [ ]:
# insert to mongo
quran.insert_many(data.to_dict('records'))

In [ ]:
x = quran.find({"SURAH_NUMBER": "67"})

Create patterns

In [ ]:
patterns = [['REL', 'V'], ['PN', 'N', 'PN'], ['REL', 'P', 'N', 'PRON'], ['REL', 'V', 'PRON'], ['N', 'PRON'], ['N'], ['COND', 'V', 'P', 'DET', 'N', 'CONJ', 'V', 'P', 'PN'], ['REL', 'V', 'PN'], ['PN'], ['N', 'DET', 'ADJ'], ['REL', 'V', 'P', 'N'], ['REL', 'V', 'PRON', 'N', 'PRON', 'P', 'N', 'PN'], ['REL', 'V', 'N', 'PRON'], ['ADJ'], ['REL', 'V', 'PRON', 'N', 'PRON', 'N', 'N', 'PN'], ['COND', 'V', 'DET', 'N'], ['N', 'DET', 'N'], ['DET', 'N'], ['REL', 'V', 'PRON', 'P', 'N', 'PN'], ['REL', 'V', 'PRON', 'N', 'PRON', 'P', 'DET', 'N', 'CONJ', 'DET', 'N'], ['REL', 'V', 'PRON', 'DET', 'N'], ['COND', 'V', 'PRON'], ['COND', 'V'], ['N', 'DET', 'N', 'PRON'], ['REL', 'V', 'PRON', 'CONJ', 'V', 'PRON', 'DET', 'N', 'CONJ', 'V', 'PRON', 'DET', 'N', 'CONJ', 'V', 'PRON', 'DET', 'N'], ['REL', 'P', 'PRON', 'DET', 'N'], ['COND', 'P', 'N', 'PRON', 'N'], ['N', 'PN'], ['N', 'CONJ', 'DET', 'N'], ['REL', 'V', 'PRON', 'N', 'PRON', 'ACC', 'PRON', 'V', 'PRON', 'REM', 'V', 'P', 'PRON', 'N', 'PRON', 'CONJ', 'V', 'PRON', 'N', 'DET', 'N', 'DET', 'N', 'CONJ', 'DET', 'N', 'CONJ', 'DET', 'N', 'CONJ', 'DET', 'N', 'CONJ', 'DET', 'N', 'P', 'DET', 'N', 'V', 'PN', 'ACC', 'PRON', 'NEG', 'N', 'EXP', 'PRON', 'CONJ', 'DET', 'N', 'CONJ', 'N', 'DET', 'N', 'N', 'P', 'DET', 'N', 'NEG', 'N', 'EXP', 'PRON', 'DET', 'N', 'DET', 'ADJ', 'ACC', 'DET', 'N', 'LOC', 'PN', 'DET', 'PN', 'REM', 'NEG', 'V', 'REL', 'V', 'PRON', 'DET', 'N', 'RES', 'P', 'N', 'REL', 'V', 'PRON', 'DET', 'N', 'N', 'LOC', 'PRON', 'REM', 'COND', 'V', 'P', 'N', 'PN', 'RSLT', 'ACC', 'PN', 'N', 'DET', 'N', 'REM', 'COND', 'V', 'PRON', 'PRON', 'RSLT', 'V', 'V', 'PRON', 'N', 'PRON', 'P', 'PN', 'CONJ', 'REL', 'V', 'PRON', 'CONJ', 'V', 'P', 'REL', 'V', 'PRON', 'DET', 'N', 'CONJ', 'DET', 'N', 'INTG', 'V', 'PRON', 'REM', 'COND', 'V', 'PRON', 'RSLT', 'CERT', 'V', 'PRON', 'CONJ', 'COND', 'V', 'PRON', 'RSLT', 'ACC', 'PREV', 'P', 'PRON', 'DET', 'N', 'REM', 'PN', 'N', 'P', 'DET', 'N', 'ACC', 'REL', 'V', 'PRON', 'P', 'N', 'PN', 'CONJ', 'V', 'PRON', 'DET', 'N', 'P', 'N', 'N', 'CONJ', 'V', 'PRON', 'REL', 'V', 'PRON', 'P', 'DET', 'N', 'P', 'DET', 'N', 'REM', 'V', 'PRON', 'P', 'N', 'ADJ', 'DEM', 'REL', 'V', 'N', 'PRON', 'P', 'DET', 'N', 'CONJ', 'DET', 'N', 'REM', 'NEG', 'P', 'PRON', 'P', 'N', 'INTG', 'NEG', 'V', 'P', 'REL', 'V', 'PRON', 'N', 'P', 'DET', 'N', 'V', 'PRON', 'P', 'N', 'PN', 'PRP', 'V', 'LOC', 'PRON', 'CONJ', 'V', 'N', 'P', 'PRON', 'CIRC', 'PRON', 'N', 'DEM', 'P', 'ACC', 'PRON', 'V', 'PRON', 'NEG', 'V', 'PRON', 'DET', 'N', 'RES', 'T', 'ADJ', 'REM', 'V', 'PRON', 'P', 'N', 'PRON', 'REL', 'V', 'PRON', 'V', 'PRON', 'REM', 'INTG', 'T', 'V', 'PRON', 'PRON', 'P', 'N', 'NEG', 'N', 'P', 'PRON', 'CONJ', 'V', 'N', 'N', 'REL', 'V', 'CIRC', 'PRON', 'NEG', 'V', 'PRON', 'V', 'PN', 'VOC', 'N', 'DET', 'N', 'V', 'DET', 'N', 'REL', 'V', 'CONJ', 'V', 'DET', 'N', 'P', 'REL', 'V', 'CONJ', 'V', 'REL', 'V', 'CONJ', 'V', 'REL', 'V', 'P', 'N', 'PRON', 'DET', 'N', 'ACC', 'PRON', 'P', 'N', 'N', 'N', 'V', 'DET', 'N', 'P', 'DET', 'N', 'CONJ', 'V', 'DET', 'N', 'P', 'DET', 'N', 'CONJ', 'V', 'DET', 'N', 'P', 'DET', 'N', 'CONJ', 'V', 'DET', 'N', 'P', 'DET', 'N', 'CONJ', 'V', 'REL', 'V', 'P', 'N', 'N', 'PRO', 'V', 'DET', 'N', 'DET', 'N', 'N', 'P', 'N', 'DET', 'N', 'REM', 'COND', 'V', 'DEM', 'RSLT', 'V', 'P', 'PN', 'P', 'N', 'RES', 'SUB', 'V', 'PRON', 'P', 'PRON', 'N', 'REM', 'V', 'PRON', 'PN', 'N', 'PRON', 'REM', 'P', 'PN', 'DET', 'N', 'V', 'COND', 'V', 'PRON', 'REL', 'P', 'N', 'PRON', 'CONJ', 'V', 'PRON', 'PRON', 'V', 'PRON', 'PN', 'REM', 'V', 'REL', 'P', 'DET', 'N', 'CONJ', 'REL', 'P', 'DET', 'N', 'REM', 'PN', 'P', 'N', 'N', 'N', 'T', 'V', 'N', 'N', 'REL', 'V', 'P', 'N', 'N', 'CONJ', 'REL', 'V', 'P', 'N', 'V', 'SUB', 'ACC', 'LOC', 'PRON', 'CONJ', 'LOC', 'PRON', 'N', 'ADJ', 'REM', 'V', 'PRON', 'PN', 'N', 'PRON', 'REM', 'PN', 'N', 'P', 'DET', 'N', 'V', 'COND', 'V', 'PRON', 'V', 'PRON', 'PN', 'RSLT', 'V', 'PRON', 'PRON', 'V', 'PRON', 'PN', 'CONJ', 'V', 'P', 'PRON', 'N', 'PRON', 'REM', 'PN', 'N', 'ADJ', 'V', 'V', 'PRON', 'PN', 'CONJ', 'DET', 'N', 'REM', 'COND', 'V', 'PRON', 'RSLT', 'ACC', 'PN', 'NEG', 'V', 'DET', 'N', 'ACC', 'PN', 'V', 'PN', 'CONJ', 'PN', 'CONJ', 'N', 'PN', 'CONJ', 'N', 'PN', 'P', 'DET', 'N', 'N', 'N', 'PRON', 'P', 'N', 'REM', 'PN', 'N', 'ADJ', 'T', 'V', 'N', 'PN', 'N', 'PRON', 'ACC', 'PRON', 'V', 'PRON', 'P', 'PRON', 'REL', 'P', 'N', 'PRON', 'N', 'REM', 'V', 'P', 'PRON', 'ACC', 'PRON', 'PRON', 'DET', 'N', 'DET', 'ADJ', 'REM', 'T', 'V', 'PRON', 'V', 'N', 'PRON', 'ACC', 'PRON', 'V', 'PRON', 'PRON', 'N', 'REM', 'PN', 'N', 'P', 'REL', 'V', 'REM', 'V', 'DET', 'N', 'P', 'DET', 'N', 'CONJ', 'ACC', 'PRON', 'V', 'PRON', 'PRON', 'PN', 'CONJ', 'ACC', 'PRON', 'V', 'PRON', 'P', 'PRON', 'CONJ', 'N', 'PRON', 'P', 'DET', 'PN', 'DET', 'ADJ', 'REM', 'V', 'PRON', 'N', 'PRON', 'P', 'N', 'ADJ', 'CONJ', 'V', 'PRON', 'N', 'ADJ', 'CONJ', 'V', 'PRON', 'PN', 'T', 'V', 'P', 'PRON', 'PN', 'DET', 'N', 'V', 'LOC', 'PRON', 'N', 'V', 'VOC', 'PN', 'INTG', 'P', 'PRON', 'DEM', 'V', 'PRON', 'P', 'N', 'PN', 'ACC', 'PN', 'V', 'REL', 'V', 'P', 'N', 'N', 'T', 'V', 'PN', 'N', 'PRON', 'V', 'N', 'PRON', 'V', 'P', 'PRON', 'P', 'N', 'PRON', 'N', 'ADJ', 'ACC', 'PRON', 'N', 'DET', 'N', 'REM', 'V', 'PRON', 'DET', 'N', 'CIRC', 'PRON', 'N', 'V', 'P', 'DET', 'N', 'ACC', 'PN', 'V', 'PRON', 'P', 'PN', 'N', 'P', 'N', 'P', 'PN', 'CONJ', 'N', 'CONJ', 'N', 'CONJ', 'N', 'P', 'DET', 'N', 'V', 'N', 'PRON', 'INTG', 'V', 'P', 'PRON', 'N', 'CIRC', 'CERT', 'V', 'PRON', 'DET', 'N', 'CONJ', 'N', 'PRON', 'N', 'V', 'P', 'DEM', 'PN', 'V', 'REL', 'V', 'V', 'N', 'PRON', 'V', 'P', 'PRON', 'N', 'V', 'N', 'PRON', 'SUB', 'NEG', 'V', 'DET', 'N', 'T', 'N', 'EXP', 'N', 'CONJ', 'V', 'N', 'PRON', 'ADJ', 'CONJ', 'V', 'P', 'DET', 'N', 'CONJ', 'DET', 'N', 'CONJ', 'T', 'V', 'DET', 'N', 'VOC', 'PN', 'ACC', 'PN', 'V', 'PRON', 'CONJ', 'V', 'PRON', 'CONJ', 'V', 'PRON', 'P', 'N', 'DET', 'N', 'VOC', 'PN', 'V', 'PRON', 'P', 'N', 'PRON', 'CONJ', 'V', 'PRON', 'CONJ', 'V', 'PRON', 'LOC', 'DET', 'N', 'DEM', 'P', 'N', 'DET', 'N', 'V', 'PRON', 'P', 'PRON', 'REM', 'NEG', 'V', 'PRON', 'LOC', 'PRON', 'T', 'V', 'PRON', 'N', 'PRON', 'INTG', 'PRON', 'V', 'PN', 'CONJ', 'NEG', 'V', 'PRON', 'LOC', 'PRON', 'T', 'V', 'PRON', 'T', 'V', 'DET', 'N', 'VOC', 'PN', 'ACC', 'PN', 'V', 'PRON', 'P', 'N', 'P', 'PRON', 'N', 'PRON', 'DET', 'PN', 'PN', 'N', 'PN', 'N', 'P', 'DET', 'N', 'CONJ', 'DET', 'N', 'CONJ', 'P', 'DET', 'N', 'CONJ', 'V', 'DET', 'N', 'P', 'DET', 'N', 'CONJ', 'N', 'CONJ', 'P', 'DET', 'N', 'V', 'N', 'PRON', 'INTG', 'V', 'P', 'PRON', 'N', 'CIRC', 'NEG', 'V', 'PRON', 'N', 'V', 'P', 'DEM', 'PN', 'V', 'REL', 'V', 'T', 'V', 'N', 'RSLT', 'ACC', 'PREV', 'V', 'P', 'PRON', 'V', 'CONJ', 'V', 'REM', 'V', 'PRON', 'DET', 'N', 'CONJ', 'DET', 'N', 'CONJ', 'DET', 'PN', 'CONJ', 'DET', 'PN', 'CONJ', 'N', 'P', 'N', 'PN', 'ACC', 'PRON', 'CERT', 'V', 'PRON', 'PRON', 'P', 'N', 'P', 'N', 'PRON', 'ACC', 'PRON', 'V', 'P', 'PRON', 'P', 'DET', 'N', 'P', 'N', 'DET', 'N', 'CONJ', 'V', 'P', 'PRON', 'CONJ', 'V', 'N', 'P', 'N', 'PN', 'CONJ', 'V', 'DET', 'N', 'CONJ', 'DET', 'N', 'CONJ', 'V', 'DET', 'N', 'P', 'N', 'PN', 'CONJ', 'V', 'PRON', 'P', 'REL', 'V', 'PRON', 'CONJ', 'REL', 'V', 'PRON', 'P', 'N', 'PRON', 'ACC', 'P', 'DEM', 'EMPH', 'N', 'P', 'PRON', 'COND', 'V', 'PRON', 'N', 'CONJ', 'N', 'P', 'REL', 'LOC', 'N', 'PRON', 'P', 'DET', 'PN', 'CONJ', 'PRP', 'V', 'P', 'PRON', 'N', 'REL', 'V', 'P', 'PRON', 'REM', 'V', 'PRON', 'PRON', 'P', 'N', 'P', 'N', 'PRON', 'REM', 'V', 'PRON', 'PN', 'CONJ', 'V', 'PRON', 'PRON', 'ACC', 'PN', 'N', 'PRON', 'CONJ', 'N', 'PRON', 'REM', 'V', 'PRON', 'PRON', 'DEM', 'N', 'ADJ', 'REM', 'T', 'V', 'PN', 'P', 'PRON', 'DET', 'N', 'V', 'INTG', 'N', 'PRON', 'P', 'PN', 'V', 'DET', 'N', 'PRON', 'N', 'PN', 'V', 'PRON', 'P', 'PN', 'REM', 'V', 'P', 'ACC', 'PRON', 'N', 'N', 'PRON', 'V', 'PRON', 'P', 'REL', 'V', 'PRON', 'CONJ', 'V', 'PRON', 'DET', 'N', 'REM', 'V', 'PRON', 'LOC', 'DET', 'N', 'REM', 'V', 'PRON', 'CONJ', 'V', 'PN', 'REM', 'PN', 'N', 'DET', 'N', 'T', 'V', 'PN', 'VOC', 'PN', 'ACC', 'PRON', 'N', 'PRON', 'CONJ', 'N', 'PRON', 'P', 'PRON', 'CONJ', 'N', 'PRON', 'P', 'REL', 'V', 'PRON', 'CONJ', 'N', 'REL', 'V', 'PRON', 'PRON', 'LOC', 'REL', 'V', 'PRON', 'P', 'N', 'DET', 'N', 'CONJ', 'P', 'PRON', 'N', 'PRON', 'CONJ', 'V', 'LOC', 'PRON', 'P', 'REL', 'V', 'PRON', 'P', 'PRON', 'V', 'PRON', 'REM', 'EXL', 'COND', 'V', 'PRON', 'RSLT', 'V', 'PRON', 'N', 'ADJ', 'P', 'DET', 'N', 'CONJ', 'DET', 'N', 'REM', 'NEG', 'P', 'PRON', 'P', 'N', 'CONJ', 'EXL', 'COND', 'V', 'PRON', 'CONJ', 'V', 'PRON', 'DET', 'N', 'RSLT', 'V', 'PRON', 'N', 'PRON', 'REM', 'PN', 'NEG', 'V', 'DET', 'N', 'DEM', 'V', 'PRON', 'P', 'PRON', 'P', 'DET', 'N', 'CONJ', 'DET', 'N', 'DET', 'ADJ', 'ACC', 'N', 'PN', 'LOC', 'PN', 'P', 'N', 'PN', 'V', 'PRON', 'P', 'N', 'CONJ', 'V', 'P', 'PRON', 'V', 'REM', 'V', 'DET', 'N', 'P', 'N', 'PRON', 'REM', 'PRO', 'V', 'P', 'DET', 'N', 'REM', 'COND', 'V', 'PRON', 'P', 'PRON', 'P', 'N', 'REL', 'V', 'PRON', 'P', 'DET', 'N', 'RSLT', 'V', 'V', 'PRON', 'V', 'N', 'PRON', 'CONJ', 'N', 'PRON', 'CONJ', 'N', 'PRON', 'CONJ', 'N', 'PRON', 'CONJ', 'N', 'PRON', 'CONJ', 'N', 'PRON', 'CONJ', 'V', 'CONJ', 'V', 'N', 'PN', 'P', 'DET', 'N', 'ACC', 'DEM', 'EMPH', 'PRON', 'DET', 'N', 'DET', 'ADJ', 'REM', 'NEG', 'P', 'N', 'RES', 'PN', 'REM', 'ACC', 'PN', 'EMPH', 'PRON', 'DET', 'N', 'DET', 'ADJ', 'REM', 'COND', 'V', 'PRON', 'RSLT', 'ACC', 'PN', 'N', 'P', 'DET', 'N', 'V', 'VOC', 'N', 'DET', 'N', 'V', 'PRON', 'P', 'N', 'ADJ', 'LOC', 'PRON', 'CONJ', 'LOC', 'PRON', 'SUB', 'NEG', 'V', 'RES', 'PN', 'CONJ', 'NEG', 'V', 'P', 'PRON', 'N', 'CONJ', 'NEG', 'V', 'N', 'PRON', 'N', 'N', 'P', 'N', 'PN', 'REM', 'COND', 'V', 'PRON', 'RSLT', 'V', 'PRON', 'V', 'PRON', 'P', 'ACC', 'PRON', 'N', 'VOC', 'N', 'DET', 'N', 'P', 'INTG', 'V', 'PRON', 'P', 'PN', 'CIRC', 'NEG', 'V', 'DET', 'PN', 'CONJ', 'DET', 'PN', 'RES', 'P', 'N', 'PRON', 'INTG', 'SUP', 'NEG', 'V', 'PRON', 'VOC', 'PRON', 'DEM', 'V', 'PRON', 'P', 'REL', 'P', 'PRON', 'P', 'PRON', 'N', 'REM', 'P', 'INTG', 'V', 'PRON', 'P', 'REL', 'V', 'P', 'PRON', 'P', 'PRON', 'N', 'REM', 'PN', 'V', 'CONJ', 'PRON', 'NEG', 'V', 'PRON', 'NEG', 'V', 'PN', 'PN', 'CONJ', 'NEG', 'PN', 'SUP', 'AMD', 'V', 'N', 'ADJ', 'CONJ', 'NEG', 'V', 'P', 'DET', 'N', 'ACC', 'N', 'DET', 'N', 'P', 'PN', 'EMPH', 'REL', 'V', 'PRON', 'PRON', 'CONJ', 'DEM', 'DET', 'N', 'CONJ', 'REL', 'V', 'PRON', 'REM', 'PN', 'N', 'DET', 'N', 'V', 'N', 'P', 'N', 'DET', 'N', 'SUB', 'V', 'PRON', 'PRON', 'REM', 'NEG', 'V', 'PRON', 'RES', 'N', 'PRON', 'CIRC', 'NEG', 'V', 'PRON', 'VOC', 'N', 'DET', 'N', 'P', 'INTG', 'V', 'PRON', 'P', 'N', 'PN', 'CIRC', 'PRON', 'V', 'PRON', 'VOC', 'N', 'DET', 'N', 'P', 'INTG', 'V', 'PRON', 'DET', 'N', 'P', 'DET', 'N', 'CONJ', 'V', 'PRON', 'DET', 'N', 'CIRC', 'PRON', 'V', 'PRON', 'REM', 'V', 'N', 'P', 'N', 'DET', 'N', 'V', 'PRON', 'P', 'REL', 'V', 'P', 'REL', 'V', 'PRON', 'T', 'DET', 'N', 'CONJ', 'V', 'PRON', 'T', 'PRON', 'ACC', 'PRON', 'V', 'PRON', 'CONJ', 'PRO', 'V', 'PRON', 'EXP', 'P', 'REL', 'V', 'N', 'PRON', 'V', 'ACC', 'DET', 'N', 'N', 'PN', 'SUB', 'V', 'N', 'N', 'REL', 'V', 'PRON', 'CONJ', 'V', 'PRON', 'PRON', 'LOC', 'N', 'PRON', 'V', 'ACC', 'DET', 'N', 'P', 'N', 'PN', 'V', 'PRON', 'REL', 'V', 'REM', 'PN', 'N', 'ADJ', 'V', 'P', 'N', 'PRON', 'REL', 'V', 'REM', 'PN', 'N', 'DET', 'N', 'DET', 'ADJ', 'REM', 'P', 'N', 'DET', 'N', 'REL', 'COND', 'V', 'PRON', 'P', 'N', 'V', 'PRON', 'P', 'PRON', 'CONJ', 'P', 'PRON', 'REL', 'COND', 'V', 'PRON', 'P', 'N', 'NEG', 'V', 'PRON', 'P', 'PRON', 'RES', 'SUB', 'V', 'PRON', 'P', 'PRON', 'N', 'DEM', 'P', 'ACC', 'PRON', 'V', 'PRON', 'V', 'P', 'PRON', 'P', 'DET', 'N', 'N', 'REM', 'V', 'PRON', 'P', 'PN', 'DET', 'N', 'CIRC', 'PRON', 'V', 'PRON', 'ANS', 'COND', 'V', 'P', 'N', 'PRON', 'CONJ', 'V', 'RSLT', 'ACC', 'PN', 'V', 'DET', 'N', 'ACC', 'REL', 'V', 'PRON', 'P', 'N', 'PN', 'CONJ', 'N', 'PRON', 'N', 'ADJ', 'DEM', 'NEG', 'N', 'P', 'PRON', 'P', 'DET', 'N', 'CONJ', 'NEG', 'V', 'PRON', 'PN', 'CONJ', 'NEG', 'V', 'P', 'PRON', 'T', 'DET', 'N', 'CONJ', 'NEG', 'V', 'PRON', 'CONJ', 'P', 'PRON', 'N', 'ADJ', 'REM', 'ACC', 'P', 'PRON', 'EMPH', 'N', 'V', 'PRON', 'N', 'PRON', 'P', 'DET', 'N', 'PRP', 'V', 'PRON', 'PRON', 'P', 'DET', 'N', 'REM', 'NEG', 'PRON', 'P', 'DET', 'N', 'CONJ', 'V', 'PRON', 'PRON', 'P', 'N', 'PN', 'REM', 'NEG', 'PRON', 'P', 'N', 'PN', 'CONJ', 'V', 'PRON', 'P', 'PN', 'DET', 'N', 'CIRC', 'PRON', 'V', 'PRON', 'NEG', 'V', 'P', 'N', 'SUB', 'V', 'PRON', 'PN', 'DET', 'N', 'CONJ', 'DET', 'N', 'CONJ', 'DET', 'N', 'CONJ', 'V', 'P', 'DET', 'N', 'V', 'PRON', 'N', 'P', 'PRON', 'P', 'N', 'PN', 'REM', 'AMD', 'V', 'PRON', 'N', 'P', 'SUB', 'V', 'PRON', 'V', 'PRON', 'DET', 'N', 'CONJ', 'P', 'SUB', 'V', 'PRON', 'V', 'PRON', 'CONJ', 'NEG', 'V', 'PRON', 'SUB', 'V', 'PRON', 'DET', 'N', 'CONJ', 'DET', 'N', 'N', 'INTG', 'V', 'PRON', 'P', 'DET', 'N', 'T', 'T', 'PRON', 'N', 'CONJ', 'T', 'V', 'PN', 'N', 'DET', 'N', 'EMPH', 'REL', 'V', 'PRON', 'PRON', 'P', 'N', 'CONJ', 'N', 'CONJ', 'V', 'PRON', 'N', 'ADJ', 'P', 'REL', 'LOC', 'PRON', 'EMPH', 'V', 'EMPH', 'P', 'PRON', 'CONJ', 'EMPH', 'V', 'EMPH', 'PRON', 'V', 'INTG', 'V', 'PRON', 'CONJ', 'V', 'PRON', 'P', 'DEM', 'N', 'PRON', 'V', 'PRON', 'V', 'PRON', 'V', 'REM', 'V', 'PRON', 'REM', 'PRON', 'LOC', 'PRON', 'P', 'DET', 'N', 'REM', 'COND', 'V', 'T', 'DEM', 'RSLT', 'DEM', 'PRON', 'DET', 'N', 'INTG', 'SUP', 'N', 'N', 'PN', 'V', 'PRON', 'CIRC', 'P', 'PRON', 'V', 'REL', 'P', 'DET', 'N', 'CONJ', 'DET', 'N', 'N', 'CONJ', 'N', 'CIRC', 'P', 'PRON', 'V', 'PRON', 'V', 'V', 'PRON', 'P', 'PN', 'CONJ', 'REL', 'V', 'P', 'PRON', 'CONJ', 'REL', 'V', 'P', 'PN', 'CONJ', 'PN', 'CONJ', 'PN', 'CONJ', 'PN', 'CONJ', 'DET', 'N', 'CONJ', 'REL', 'V', 'PN', 'CONJ', 'PN', 'CONJ', 'DET', 'N', 'P', 'N', 'PRON', 'NEG', 'V', 'LOC', 'N', 'P', 'PRON', 'REM', 'PRON', 'P', 'PRON', 'N', 'REM', 'COND', 'V', 'N', 'DET', 'PN', 'N', 'RSLT', 'NEG', 'V', 'P', 'PRON', 'REM', 'PRON', 'P', 'DET', 'N', 'P', 'DET', 'N', 'INTG', 'V', 'PN', 'N', 'V', 'PRON', 'T', 'N', 'PRON', 'CONJ', 'V', 'PRON', 'ACC', 'DET', 'N', 'N', 'CONJ', 'V', 'PRON', 'DET', 'N', 'REM', 'PN', 'NEG', 'V', 'DET', 'N', 'DET', 'ADJ', 'DEM', 'N', 'PRON', 'ACC', 'P', 'PRON', 'N', 'PN', 'CONJ', 'DET', 'N', 'CONJ', 'DET', 'N', 'N', 'N', 'P', 'PRON', 'NEG', 'V', 'P', 'PRON', 'DET', 'N', 'CONJ', 'NEG', 'PRON', 'V', 'PRON', 'EXP', 'REL', 'V', 'PRON', 'P', 'N', 'DEM', 'CONJ', 'V', 'PRON', 'REM', 'ACC', 'PN', 'N', 'ADJ', 'ACC', 'REL', 'V', 'PRON', 'T', 'N', 'PRON', 'CONJ', 'V', 'PRON', 'N', 'NEG', 'V', 'N', 'PRON', 'REM', 'DEM', 'PRON', 'DET', 'N', 'ACC', 'REL', 'V', 'PRON', 'CONJ', 'V', 'PRON', 'CIRC', 'PRON', 'N', 'REM', 'NEG', 'V', 'P', 'N', 'PRON', 'N', 'DET', 'N', 'N', 'CIRC', 'COND', 'V', 'P', 'PRON', 'DEM', 'P', 'PRON', 'N', 'ADJ', 'CONJ', 'NEG', 'P', 'PRON', 'P', 'N']]

In [ ]:
for i in range(len(patterns)):
    patterns[i] = {"pattern": patterns[i]}
                                      
patterns

In [ ]:
# insert patterns
mydb["patterns"].insert_many(patterns)

In [ ]:
x = quran.find({"SURAH_NUMBER": "67"})

????

In [ ]:
patterns = list(mydb["patterns"].find())

for pattern in patterns:
    stripped_spaces = pattern["pattern"].replace(" ", "")
    mydb["patterns"].update_one({"pattern": pattern["pattern"]}, {"$set" : {"pattern": stripped_spaces}})

## 6. Arabic Entity Classifier Using Patterns

In [ ]:
#!/usr/bin/env python
# coding: utf-8

# In[14]:

import pandas as pd

def group(ayats):
        
    length = len(ayats)
    i = 0

    grouppedAyats = [[]]

    index = 0
    for row in ayats:

        # tokenizing location
        if index < length-1:
            currentLocation = row["AYAT_NUMBER"]
            nextLocation = ayats[index+1]['AYAT_NUMBER']

            if index == length-2 or currentLocation != nextLocation:
                i = i+1
                grouppedAyats.append([])
            
            ayats[index]['AYAT_NUMBER'] = i
            
            words = {
                'OPEN TAG' : '',
                'AYAT' : int(row['AYAT_NUMBER']),
                'ARAB' : row['ARAB'],
                'TAG' : row['TAG'],
                'WORD_NUMBER' : row['WORD_NUMBER'],
                'AYAT_NUMBER' : row['AYAT_NUMBER'],
                'CLOSE TAG' : ''
            }
            
            grouppedAyats[i].append(words)

        index += 1
        
    return grouppedAyats

def ungroup(ayats):

    ungrouppedAyats = []

    for ayat in ayats:
        for word in ayat:
            ungrouppedAyats.append(word)

    return ungrouppedAyats

def classify(patterns, ayats):

    # Prepare data
    ayats = group(ayats)

    # Rule based logic
    ayatIndex = 0
    entityIndex = 0

    for ayat in ayats:
        for pattern in patterns:
            patternLength = len(pattern)
            for wordIndex in range(len(ayat) - patternLength):
                # Get Array of words based on the pattern length
                wordTagsArray = []
                for wordOfArrayIndex in range(patternLength):
                    wordTagsArray.append(ayat[wordIndex+wordOfArrayIndex]['TAG'])
                if wordTagsArray == pattern:
                    print('foundd')
                    ayat[wordIndex]['OPEN TAG'] += str(entityIndex) + '('
                    ayat[wordIndex+patternLength]['CLOSE TAG'] += str(entityIndex) + ')'
                    entityIndex += 1
        ayatIndex += 1

    return ungroup(ayats)

# %%